In [ ]:
from pycaret.clustering import *
import pandas as pd
import numpy as np   # <-- IMPORTANTE
from sklearn.metrics import silhouette_score, calinski_harabasz_score, davies_bouldin_score

# Cargar dataset
ruta = r"C:\Users\FABIO\Downloads\dataset_hoteles_tunja_50000vlucy.csv"
df = pd.read_csv(ruta)

# Seleccionar solo columnas numéricas
df_num = df.select_dtypes(include=[np.number])

# Inicializar experimento
exp_clust = setup(
    data=df_num,
    normalize=True,
    session_id=123,
    verbose=False
)

# Lista de modelos a probar
modelos = ['kmeans']

resultados = []

for modelo in modelos:
    try:
        m = create_model(modelo)
        asignado = assign_model(m, verbose=False)
        
        # Si no genera clusters válidos, puede fallar
        labels = asignado['Cluster']
        if len(set(labels)) > 1:  # al menos 2 clusters
            sil = silhouette_score(asignado.drop(columns=['Cluster']), labels)
            ch = calinski_harabasz_score(asignado.drop(columns=['Cluster']), labels)
            db = davies_bouldin_score(asignado.drop(columns=['Cluster']), labels)
            resultados.append([modelo, sil, ch, db])
    except Exception as e:
        print(f"Error con modelo {modelo}: {e}")

# Mostrar comparativa
res_df = pd.DataFrame(resultados, columns=['Modelo', 'Silhouette', 'Calinski-Harabasz', 'Davies-Bouldin'])

print("\n=== Comparación de Modelos de Clustering ===\n")
print(res_df.to_string(index=False))

# Entrenar KMeans con 2 clusters
kmeans2 = create_model('kmeans', num_clusters=2)

# Asignar clusters al dataset
asignado2 = assign_model(kmeans2, verbose=False)

# Evaluar métricas
labels = asignado2['Cluster']
X = asignado2.drop(columns=['Cluster'])

from sklearn.metrics import silhouette_score, calinski_harabasz_score, davies_bouldin_score

sil = silhouette_score(X, labels)
ch = calinski_harabasz_score(X, labels)
db = davies_bouldin_score(X, labels)

print("Resultados KMeans con 2 clusters:")
print(f"Silhouette: {sil:.4f}")
print(f"Calinski-Harabasz: {ch:.4f}")
print(f"Davies-Bouldin: {db:.4f}")
plot_model(kmeans2, plot='cluster')

rangos = range(2, 11)  # de 2 a 10 clusters
resultados_kmeans = []

for k in rangos:
    modelo = create_model('kmeans', num_clusters=k)
    asignado = assign_model(modelo, verbose=False)
    labels = asignado['Cluster']
    X = asignado.drop(columns=['Cluster'])
    
    sil = silhouette_score(X, labels)
    ch = calinski_harabasz_score(X, labels)
    db = davies_bouldin_score(X, labels)
    resultados_kmeans.append([k, sil, ch, db])

res_kmeans_df = pd.DataFrame(resultados_kmeans, columns=['k', 'Silhouette', 'Calinski-Harabasz', 'Davies-Bouldin'])
print(res_kmeans_df)

import matplotlib.pyplot as plt

# Graficar Silhouette
plt.figure(figsize=(12, 4))

plt.subplot(1, 3, 1)
plt.plot(res_kmeans_df['k'], res_kmeans_df['Silhouette'], marker='o')
plt.title("Silhouette Score")
plt.xlabel("Número de clusters (k)")
plt.ylabel("Silhouette")

# Graficar Calinski-Harabasz
plt.subplot(1, 3, 2)
plt.plot(res_kmeans_df['k'], res_kmeans_df['Calinski-Harabasz'], marker='o')
plt.title("Calinski-Harabasz")
plt.xlabel("Número de clusters (k)")
plt.ylabel("CH Index")

# Graficar Davies-Bouldin
plt.subplot(1, 3, 3)
plt.plot(res_kmeans_df['k'], res_kmeans_df['Davies-Bouldin'], marker='o')
plt.title("Davies-Bouldin")
plt.xlabel("Número de clusters (k)")
plt.ylabel("DB Index")

plt.tight_layout()
plt.show()




=== Comparación de Modelos de Clustering ===

Modelo  Silhouette  Calinski-Harabasz  Davies-Bouldin
kmeans    0.035502         2504.82125       18.214863


Resultados KMeans con 2 clusters:
Silhouette: -0.0000
Calinski-Harabasz: 17.4281
Davies-Bouldin: 40.9346


In [2]:
# Determinar el mejor modelo automáticamente
# Criterios: mayor Silhouette, mayor Calinski-Harabasz, menor Davies-Bouldin
mejor_modelo = res_df.loc[res_df['Silhouette'].idxmax()]
print(f"\nEl mejor modelo según el Silhouette Score es: {mejor_modelo['Modelo']}")
print(f"Métricas:\nSilhouette: {mejor_modelo['Silhouette']:.4f}\nCalinski-Harabasz: {mejor_modelo['Calinski-Harabasz']:.4f}\nDavies-Bouldin: {mejor_modelo['Davies-Bouldin']:.4f}")


El mejor modelo según el Silhouette Score es: hclust
Métricas:
Silhouette: 0.1096
Calinski-Harabasz: 20.3712
Davies-Bouldin: 1.7764
